## Overall percentile of queue and execution time

In [0]:
WITH queries AS (
     SELECT
          date_trunc('day',start_time) as period
          , ROUND(queue_time::NUMERIC / 1000000,2) queue_s
          , ROUND(execution_time::NUMERIC / 1000000,2) exec_s
     FROM sys_query_history q  
     WHERE q.user_id > 1
)
SELECT
      period
      , COUNT(*) AS queries
      , ROUND(PERCENTILE_CONT(0.25) WITHIN GROUP (ORDER BY exec_s),2) AS p25_exec_s
      , ROUND(PERCENTILE_CONT(0.50) WITHIN GROUP (ORDER BY exec_s),2) AS p50_exec_s
      , ROUND(PERCENTILE_CONT(0.75) WITHIN GROUP (ORDER BY exec_s),2) AS p75_exec_s
      , ROUND(PERCENTILE_CONT(0.90) WITHIN GROUP (ORDER BY exec_s),2) AS p90_exec_s
      , ROUND(PERCENTILE_CONT(0.95) WITHIN GROUP (ORDER BY exec_s),2) AS p95_exec_s
      , ROUND(PERCENTILE_CONT(0.99) WITHIN GROUP (ORDER BY exec_s),2) AS p99_exec_s
      , ROUND(PERCENTILE_CONT(0.999) WITHIN GROUP (ORDER BY exec_s),2) AS p999_exec_s
      , MAX(exec_s) AS max_exec_s
      , MAX(queue_s) AS max_queue_s
      , AVG(exec_s) AS avg_exec_s
      , AVG(queue_s) AS avg_queue_s
      , SUM(exec_s) AS sum_exec_s
      , SUM(queue_s) AS sum_queue_s
FROM queries
WHERE period::date>=getdate()-30
GROUP BY 1
ORDER BY 1
;

## Percentile Query

In [0]:
with elapsed as (select trunc(start_time) as date
, avg( elapsed_time/1000000) as avg_elapsed_time_s
, percentile_cont(.5) within group (order by elapsed_time/1000000) as P50_elapsed_time_s
, percentile_cont(.80) within group (order by elapsed_time/1000000) as P80_elapsed_time_s
, percentile_cont(.90) within group (order by elapsed_time/1000000) as P90_elapsed_time_s
, percentile_cont(.95) within group (order by elapsed_time/1000000) as P95_elapsed_time_s
, percentile_cont(.99) within group (order by elapsed_time/1000000) as P99_elapsed_time_s
, percentile_cont(.999) within group (order by elapsed_time/1000000) as P999_elapsed_time_s
, percentile_cont(1) within group (order by elapsed_time/1000000) as P100_elapsed_time_s
from sys_query_history where user_id <>1 group by 1)

, queue as (
select
trunc(start_time) as date
, count(query_id) as cnt_query
, avg( queue_time/1000000) as avg_queue_time_s
, percentile_cont(.5) within group (order by queue_time/1000000) as P50_queue_time_s
, percentile_cont(.80) within group (order by queue_time/1000000) as P80_queue_time_s
, percentile_cont(.90) within group (order by queue_time/1000000) as P90_queue_time_s
, percentile_cont(.95) within group (order by queue_time/1000000) as P95_queue_time_s
, percentile_cont(.99) within group (order by queue_time/1000000) as P99_queue_time_s
, percentile_cont(.999) within group (order by queue_time/1000000) as P999_queue_time_s
, percentile_cont(1) within group (order by queue_time/1000000) as P100_elapsed_time_s
from sys_query_history where user_id <>1 group by 1)

, exec as (
select trunc(start_time) as date
, avg( queue_time/1000000) as avg_execution_time_s
, percentile_cont(.5) within group (order by execution_time/1000000) as P50_execution_time_s
, percentile_cont(.80) within group (order by execution_time/1000000) as P80_execution_time_s
, percentile_cont(.90) within group (order by execution_time/1000000) as P90_execution_time_s
, percentile_cont(.95) within group (order by execution_time/1000000) as P95_execution_time_s
, percentile_cont(.99) within group (order by execution_time/1000000) as P99_execution_time_s
, percentile_cont(.999) within group (order by execution_time/1000000) as P999_execution_time_s
, percentile_cont(1) within group (order by execution_time/1000000) as P100_execution_time_s
from sys_query_history where user_id <>1 group by 1 )

select
a.date
, a.cnt_query
, a.avg_queue_time_s
, a.P50_queue_time_s
, a.P80_queue_time_s
, a.P90_queue_time_s
, a.P95_queue_time_s
, a.P99_queue_time_s
, a.P999_queue_time_s
, a. P100_elapsed_time_s
, b.avg_execution_time_s
, b.P50_execution_time_s
, b.P80_execution_time_s
, b.P90_execution_time_s
, b.P95_execution_time_s
, b.P99_execution_time_s
, b.P999_execution_time_s
, b.P100_execution_time_s
, c.avg_elapsed_time_s
, c.P50_elapsed_time_s
, c.P80_elapsed_time_s
, c.P90_elapsed_time_s
, c.P95_elapsed_time_s
, c.P99_elapsed_time_s
, c.P999_elapsed_time_s
, c.P100_elapsed_time_s
from queue a
inner join exec b on a. date = b.date
inner join elapsed c on a.date = c.date
order by 1;

## Top Queries by cumulative execution time on Amazon Redshift Provisioned

In [0]:
SELECT 
    qry_md5
    ,user_id 
    ,count(distinct start_time::date) as days_executed
    ,count(query_id) AS n_qry
    ,sum(failed) as aborted_count
    ,max(left(query_text, 120)) AS query_text
    ,min(queue_seconds) AS min_queue_s
    ,max(queue_seconds) AS max_queue_s
    ,avg(queue_seconds) AS avg_queue_s
    ,sum(queue_seconds) AS total_queue_s 
    ,min(run_seconds) AS min_exec_s
    ,max(run_seconds) AS max_exec_s
    ,avg(run_seconds) AS avg_exec_s
    ,sum(run_seconds) AS total_exec_s 
    ,min(elapsed_seconds) AS min_elapsed_s
    ,max(elapsed_seconds) AS max_elapsed_s
    ,avg(elapsed_seconds) AS avg_elapsed_s
    ,sum(elapsed_seconds) AS total_elapsed_s 
    ,min(start_time)::DATE AS first_run
    ,max(start_time)::DATE AS last_run
    ,max(query_id) as example_query
FROM (
    SELECT q.user_id
        ,query_label
        ,q.query_id
        ,trim(database_name) AS DATABASE
        ,trim(query_text) AS query_text
        ,md5(trim(left(query_text,500))) AS qry_md5
        ,q.start_time
        ,q.end_time
        ,ROUND(execution_time::NUMERIC / 1000000,3) run_seconds
        ,ROUND(queue_time::NUMERIC / 1000000,3) queue_seconds
        ,ROUND(elapsed_time::NUMERIC / 1000000,3) elapsed_seconds
        ,case when status = 'failed' then 1 else 0 end as failed
    from sys_query_history q 
    WHERE q.user_id > 1
     AND q.start_time::date >=getdate()-30
    )
GROUP BY 1,2
ORDER BY total_elapsed_s DESC limit 50;

## Concurrency Scaling cost monitoring sample script. Replace <user_mapping_business_unit>

In [0]:
select
to_char(convert_timezone(‘America/New_York’,q.starttime),‘YYYY/MM/DD’),
U.business_unit,
count(1) query_per_day,
sum(case when concurrency_scaling_status=1 then 1 else 0 end) cs_query_count,
sum(case when concurrency_scaling_status>1 then 1 else 0 end) cs_invalidquery_count ,
sum(total_exec_time/60/1000000) total_exec_time_in_min,
max(total_queue_time/60/1000000) max_queue_time_in_min,
sum(total_queue_time/60/1000000) total_queue_time_in_min
from stl_query q, stl_wlm_query ms, <user_mapping_business_unit> U
WHERE 1=1
AND q.query = ms.query
AND q.userid != 1
AND q.userid=U.userid
AND q.database = current_database()
GROUP BY to_char(convert_timezone(‘America/New_York’,q.starttime), ‘YYYY/MM/DD’)
ORDER BY 1 ;